In [7]:
#Import Libraries
from selenium import webdriver
from selenium.webdriver.support.ui import Select
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException,TimeoutException
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import StaleElementReferenceException
import pandas as pd
import lxml
import os
import time
import datetime
import json

In [8]:
#Start Timmer
start = time.time()

#Set Output Folder
output_folder = datetime.datetime.now().strftime("Date-%Y-%m-%d-Time-%H-%M-%S")
if not os.path.exists(output_folder):
    os.makedirs(output_folder)

In [9]:
#Start Chrome
driver = webdriver.Chrome()
driver.implicitly_wait(20) # seconds

#Prepare URL
protocol = "https://"
url = protocol + "rhreporting.nic.in/netiay/FinancialProgressReport/finProgress_newRpt.aspx"
params = {
    'params': 0
}
for key, value in params.items():
    url = url #+ "&" + key + "=" + str(value)

#Playing with headers
my_referer = url
UserAgent = 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/39.0.2171.95 Safari/537.36'
mod_headers = {'referer': my_referer, 'User-Agent':UserAgent}

#Start Chrome
driver.get(url)

In [10]:
# Select List
year_select_name = 'ctl00$ContentPlaceHolder1$ddl_finYear'
iay_radio_name = 'ctl00$ContentPlaceHolder1$rdlScheme'
excel_button = 'ctl00$ContentPlaceHolder1$btnExport'
content_table_class = 'table_s'

In [11]:
#Build State List
def build_list(element_name):
    temp_list = driver.find_element_by_name(element_name).find_elements_by_xpath(".//option")[1:]
    _list = []
    #loop over each option
    for x in temp_list:
        d = {}
        d['text'] = x.text
        d['value'] = x.get_attribute('value')
        _list.append(d)
        #print("_list index:",i,d)
    return _list

def check_table():
    #Wait for Table to Load fully
    element_present = EC.presence_of_element_located((By.CSS_SELECTOR, '.'+content_table_class))            
    WebDriverWait(driver, 2).until(element_present)
    
#Check Submit button
def delete_excel():
    driver.execute_script("return document.getElementsByName('" + excel_button + "')[0].remove()")
def check_excel():
    WebDriverWait( driver, 2 ).until( EC.visibility_of_element_located( ( By.NAME, excel_button ) ) )

In [12]:
#Start Chrome
driver.get(url)
element = WebDriverWait(driver, 10).until(
    EC.element_to_be_clickable((By.NAME, year_select_name))
)
element.find_element_by_xpath(".//option[@value='0']").click()
yearlist = build_list(year_select_name)[7:8]
print(yearlist)
for year in yearlist:
    print("--Scrapping data for Year: ", year['text'])
    #Start Chrome
    driver.get(url)
    #Year Selection
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(".//option[@value='0']").click()
    year_query = ".//option[@value='" + year['value'] + "']"
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, year_select_name))
    )
    element.find_element_by_xpath(year_query).click()
    
    #DataStore
    df_list = []
    
    element = WebDriverWait(driver, 10).until(
        EC.element_to_be_clickable((By.NAME, iay_radio_name))
    )
    driver.find_elements_by_name(iay_radio_name)[1].click()
    
    #state select
    check_table()
    temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[3:-2]
    states = []
    for row in temp_list:
        try:
            x = {}
            td = row.find_elements_by_xpath(".//td")[1]
            x['name'] = td.text
            x['link'] = td.find_element_by_tag_name("a").get_attribute("href")
            states.append(x)
        except Exception as e:
            print("Error while parsing table data |", e)
    for state in states:
        print("----Scrapping data for State: ", state['name'])
        driver.get(state['link'])
        check_table()
        temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
        districts = []
        for row in temp_list:
            x = {}            
            x['name'] = row.find_elements_by_xpath(".//td")[1].text
            x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
            districts.append(x)
        for district in districts:
            print("------Scrapping data for District: ", district['name'])
            driver.get(district['link'])
            check_table()
            temp_list = driver.find_element_by_class_name(content_table_class).find_elements_by_xpath(".//tr")[4:-1]
            blocks = []
            for row in temp_list:
                x = {}            
                x['name'] = row.find_elements_by_xpath(".//td")[1].text
                x['link'] =row.find_elements_by_xpath(".//td")[1].find_element_by_tag_name("a").get_attribute("href")
                blocks.append(x)
            
            for block in blocks:
                print("--------Scrapping data for Block: ", block['name'])
                driver.get(block['link'])
                check_table()
                html_table = driver.find_element_by_class_name(content_table_class).get_attribute('outerHTML')
                df = pd.read_html(html_table, header=3)[0]
                df = df[:-1]
                #df.columns = table_head
                df['Financial Year'] = year['text']
                df['State Name'] = state['name']
                df['District Name'] = district['name']
                df['Block Name'] = block['name']
                df_list.append(df)
                #except Exception as e:
                #    print("Error while table data |", e)
                
    #merge all dataframes to master dataframe
    df = pd.concat(df_list)
    df.drop(df.columns[0],axis=1,inplace=True)
    df = df.reset_index()
    #Save Scrapped File
    df.to_csv(os.path.join(output_folder, year['text']+'_Scrapped_Data.csv'), encoding='utf-8', index=False)

[{'text': '2017-2018', 'value': '2017-2018 '}]
--Scrapping data for Year:  2017-2018
Error while parsing table data | Message: no such element: Unable to locate element: {"method":"tag name","selector":"a"}
  (Session info: chrome=66.0.3359.181)
  (Driver info: chromedriver=2.35.528161 (5b82f2d2aae0ca24b877009200ced9065a772e73),platform=Windows NT 10.0.17134 x86_64)

----Scrapping data for State:  ARUNACHAL PRADESH
----Scrapping data for State:  ASSAM
------Scrapping data for District:  BAKSA
--------Scrapping data for Block:  Barama
--------Scrapping data for Block:  Baska
--------Scrapping data for Block:  Dhamdhama
--------Scrapping data for Block:  Gobardhana(BTC)
--------Scrapping data for Block:  Goreswar
--------Scrapping data for Block:  Jalah(BTC)
--------Scrapping data for Block:  Nagrijuli
--------Scrapping data for Block:  Tamulpur
------Scrapping data for District:  BARPETA
--------Scrapping data for Block:  BAJALI
--------Scrapping data for Block:  BARPETA
--------Scrappi

--------Scrapping data for Block:  KARUNABARI
--------Scrapping data for Block:  LAKHIMPUR
--------Scrapping data for Block:  NARAYANPUR
--------Scrapping data for Block:  NOWBOICHA
--------Scrapping data for Block:  TELAHI
------Scrapping data for District:  Morigaon
--------Scrapping data for Block:  BATADRABA MORIGAON PART
--------Scrapping data for Block:  BHURBANDHA
--------Scrapping data for Block:  DOLONGGHAT MORIGAON PART
--------Scrapping data for Block:  KAPILI
--------Scrapping data for Block:  LAHARIGHAT
--------Scrapping data for Block:  MAYONG
--------Scrapping data for Block:  MOIRABARI
------Scrapping data for District:  NAGAON
--------Scrapping data for Block:  Bajiagaon
--------Scrapping data for Block:  Barhampur
--------Scrapping data for Block:  Batadraba
--------Scrapping data for Block:  Binakandi
--------Scrapping data for Block:  Dhalpukhuri
--------Scrapping data for Block:  Dolongghat
--------Scrapping data for Block:  Jugijan
--------Scrapping data for Block

--------Scrapping data for Block:  CHAKKI
--------Scrapping data for Block:  CHAUSA
--------Scrapping data for Block:  CHOUGAI
--------Scrapping data for Block:  DUMRAON
--------Scrapping data for Block:  ITARHI
--------Scrapping data for Block:  KESATH
--------Scrapping data for Block:  NAWANAGAR
--------Scrapping data for Block:  RAJPUR
--------Scrapping data for Block:  SIMRI
------Scrapping data for District:  DARBHANGA
--------Scrapping data for Block:  ALINAGAR
--------Scrapping data for Block:  BAHADURPUR
--------Scrapping data for Block:  BAHERI
--------Scrapping data for Block:  BENIPUR
--------Scrapping data for Block:  BIRAUL
--------Scrapping data for Block:  DARBHANGA
--------Scrapping data for Block:  GAURABAURAM
--------Scrapping data for Block:  GHANSHYAMPUR
--------Scrapping data for Block:  HANUMAN NAGAR
--------Scrapping data for Block:  HAYAGHAT
--------Scrapping data for Block:  JALE
--------Scrapping data for Block:  KEOTIRUNWAY
--------Scrapping data for Block:  

------Scrapping data for District:  MUZAFFARPUR
--------Scrapping data for Block:  AURAI
--------Scrapping data for Block:  Bandra
--------Scrapping data for Block:  BOCHAHAN
--------Scrapping data for Block:  GAIGHAT
--------Scrapping data for Block:  KANTI
--------Scrapping data for Block:  KATRA
--------Scrapping data for Block:  KURHANI
--------Scrapping data for Block:  MARWAN
--------Scrapping data for Block:  MINAPUR
--------Scrapping data for Block:  MOTIPUR
--------Scrapping data for Block:  MURAUL
--------Scrapping data for Block:  MUSHAHARI
--------Scrapping data for Block:  PAROO
--------Scrapping data for Block:  SAHEBGANJ
--------Scrapping data for Block:  Sakra
--------Scrapping data for Block:  SARAIYA
------Scrapping data for District:  NALANDA
--------Scrapping data for Block:  ASTHAWAN BLOCK
--------Scrapping data for Block:  BEN
--------Scrapping data for Block:  BIHARSARIF
--------Scrapping data for Block:  BIND BLOCK
--------Scrapping data for Block:  CHANDI BLOCK

--------Scrapping data for Block:  SINGHIA
--------Scrapping data for Block:  SIVAJEE NAGAR
--------Scrapping data for Block:  SMASTIPUR
--------Scrapping data for Block:  TAJPUR
--------Scrapping data for Block:  UJIYARPUR
--------Scrapping data for Block:  VIDYAPATI NAGAR
--------Scrapping data for Block:  WARISNAGAR
------Scrapping data for District:  SARAN
--------Scrapping data for Block:  AMNOUR
--------Scrapping data for Block:  BANIAPUR
--------Scrapping data for Block:  CHAPRA
--------Scrapping data for Block:  DARIAPUR
--------Scrapping data for Block:  DIGHWARA
--------Scrapping data for Block:  EKMA
--------Scrapping data for Block:  GARKHA
--------Scrapping data for Block:  ISUAPUR
--------Scrapping data for Block:  JALALPUR
--------Scrapping data for Block:  LAHLADPUR
--------Scrapping data for Block:  MAKER
--------Scrapping data for Block:  MANJHI
--------Scrapping data for Block:  MARHAURA
--------Scrapping data for Block:  MASHRAKH
--------Scrapping data for Block:  N

...

--------Scrapping data for Block:  Rayadurg
--------Scrapping data for Block:  Roddam
--------Scrapping data for Block:  Rolla
--------Scrapping data for Block:  Settur
--------Scrapping data for Block:  Singanamala
--------Scrapping data for Block:  Somandepalle
--------Scrapping data for Block:  Tadimarri
--------Scrapping data for Block:  Tadpatri
--------Scrapping data for Block:  Talupula
--------Scrapping data for Block:  Uravakonda
--------Scrapping data for Block:  Vajrakarur
--------Scrapping data for Block:  Vidapanakal
--------Scrapping data for Block:  Yadiki
--------Scrapping data for Block:  Yellanur
------Scrapping data for District:  CHITTOOR
--------Scrapping data for Block:  Baireddi Palle
--------Scrapping data for Block:  Buchinaidu Khandriga
--------Scrapping data for Block:  Chandragiri
--------Scrapping data for Block:  Chinnagottigallu
--------Scrapping data for Block:  Chittoor
--------Scrapping data for Block:  Gangadhara Nellore
--------Scrapping data for Blo

--------Scrapping data for Block:  Kollur
--------Scrapping data for Block:  Krosuru
--------Scrapping data for Block:  Machavaram
--------Scrapping data for Block:  Macherla
--------Scrapping data for Block:  Mangalagiri
--------Scrapping data for Block:  Medikonduru
--------Scrapping data for Block:  Muppalla
--------Scrapping data for Block:  Nadendla
--------Scrapping data for Block:  Nagaram
--------Scrapping data for Block:  Nakarikallu
--------Scrapping data for Block:  Narasaraopeta
--------Scrapping data for Block:  Nizampatnam
--------Scrapping data for Block:  Nuzendla
--------Scrapping data for Block:  Pedakakani
--------Scrapping data for Block:  Pedakurapadu
--------Scrapping data for Block:  Pedanandipadu
--------Scrapping data for Block:  Phirangipuram
--------Scrapping data for Block:  Piduguralla
--------Scrapping data for Block:  Pittalavanipalem
--------Scrapping data for Block:  Ponnur
--------Scrapping data for Block:  Prathipadu
--------Scrapping data for Block: 

--------Scrapping data for Block:  Vidavalur
--------Scrapping data for Block:  Vinjamur
------Scrapping data for District:  PRAKASAM
--------Scrapping data for Block:  Addanki
--------Scrapping data for Block:  Ardhaveedu
--------Scrapping data for Block:  Ballikuruva
--------Scrapping data for Block:  Bestavaripeta
--------Scrapping data for Block:  Chadrasekarapuram
--------Scrapping data for Block:  Chimakurthi
--------Scrapping data for Block:  Chinaganjam
--------Scrapping data for Block:  Chirala
--------Scrapping data for Block:  Cumbum
--------Scrapping data for Block:  Darsi
--------Scrapping data for Block:  Donakonda
--------Scrapping data for Block:  Dornala
--------Scrapping data for Block:  Giddaluru
--------Scrapping data for Block:  Gudluru
--------Scrapping data for Block:  Hanumanthunipadu
--------Scrapping data for Block:  Inkollu
--------Scrapping data for Block:  Janakavarampanguluru
--------Scrapping data for Block:  Kandukur
--------Scrapping data for Block:  Ka

--------Scrapping data for Block:  Buttayagudem
--------Scrapping data for Block:  Chagallu
--------Scrapping data for Block:  Chintalapudi
--------Scrapping data for Block:  Denduluru
--------Scrapping data for Block:  Devarapalle
--------Scrapping data for Block:  Dwaraka Tirumala
--------Scrapping data for Block:  Eluru
--------Scrapping data for Block:  Ganapavaram
--------Scrapping data for Block:  Gopalapuram
--------Scrapping data for Block:  Iragavaram
--------Scrapping data for Block:  Jangareddigudem
--------Scrapping data for Block:  Jeelugumilli
--------Scrapping data for Block:  Kalla
--------Scrapping data for Block:  Kamavarapukota
--------Scrapping data for Block:  Kovvur
--------Scrapping data for Block:  Koyyalagudem
--------Scrapping data for Block:  Lingapalem
--------Scrapping data for Block:  Mogalthur
--------Scrapping data for Block:  Nallajerla
--------Scrapping data for Block:  Narasapuram
--------Scrapping data for Block:  Nidadavole
--------Scrapping data fo

--------Scrapping data for Block:  Srirangapatna
------Scrapping data for District:  Mysuru
--------Scrapping data for Block:  Heggadadevanakote
--------Scrapping data for Block:  Hunsur
--------Scrapping data for Block:  Krishnarajanagara
--------Scrapping data for Block:  Mysuru
--------Scrapping data for Block:  Nanjangud
--------Scrapping data for Block:  Periyapatna
--------Scrapping data for Block:  T Narasipura
------Scrapping data for District:  Raichur
--------Scrapping data for Block:  Deodurga
--------Scrapping data for Block:  Lingasugur
--------Scrapping data for Block:  Manvi
--------Scrapping data for Block:  Raichur
--------Scrapping data for Block:  Sindhanur
------Scrapping data for District:  Ramanagara
--------Scrapping data for Block:  Chennapatna
--------Scrapping data for Block:  Kanakapura
--------Scrapping data for Block:  Magadi
--------Scrapping data for Block:  Ramanagara
------Scrapping data for District:  Shivamogga
--------Scrapping data for Block:  Bhadr